#AnimateDiffPipeline

In [ ]:
!pip install --upgrade transformers accelerate diffusers imageio-ffmpeg
import torch
from diffusers import AnimateDiffPipeline, MotionAdapter, EulerDiscreteScheduler
from diffusers.utils import export_to_gif
from huggingface_hub import hf_hub_download
from safetensors.torch import load_file

device = "cuda"
dtype = torch.float16

step = 4  # Options: [1,2,4,8]
repo = "ByteDance/AnimateDiff-Lightning"
ckpt = f"animatediff_lightning_{step}step_diffusers.safetensors"
base = "emilianJR/epiCRealism"  # Choose to base model.

adapter = MotionAdapter().to(device, dtype)
adapter.load_state_dict(load_file(hf_hub_download(repo ,ckpt), device=device))
pipe = AnimateDiffPipeline.from_pretrained(base, motion_adapter=adapter, torch_dtype=dtype).to(device)
pipe.scheduler = EulerDiscreteScheduler.from_config(pipe.scheduler.config, timestep_spacing="trailing", beta_schedule="linear")

output = pipe(prompt="crack two eggs into a bowl", guidance_scale=1.0, num_inference_steps=step)
export_to_gif(output.frames[0], "animation.gif")

#Fine-tuning


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import torch
import torch.nn.functional as F
from torch.optim import AdamW
from tqdm import tqdm
from diffusers import AnimateDiffPipeline, MotionAdapter
from huggingface_hub import hf_hub_download
from safetensors.torch import load_file

# Set up the device
device = "cuda" if torch.cuda.is_available() else "cpu"
dtype = torch.float16

In [ ]:
import os
import json
import glob
import torch
from torch.utils.data import Dataset, DataLoader
from torchvision import transforms
from PIL import Image

# Data path
frame_dir = "/content/drive/Shareddrives/DATA 298B Team 8/298A/processed_data/train"
annotation_path = "/content/drive/Shareddrives/DATA 298B Team 8/298A/youcook/annotations/youcookii_annotations_trainval.json"
os.makedirs(frame_dir, exist_ok=True)

class YouCook2Dataset(Dataset):
    def __init__(self, annotation_path, frame_path, transform=None):
        with open(annotation_path, "r") as f:
            self.annotations = json.load(f)
        self.frame_path = frame_path
        self.transform = transform or transforms.Compose([
            transforms.Resize((256, 256)),
            transforms.ToTensor()
        ])

        # Get all video IDs in `frame_dir`
        self.existing_video_ids = set([f.split("_sentence")[0] for f in os.listdir(self.frame_path) if "_frames" in f])

        # Load data
        self.data = self.prepare_data()

    def prepare_data(self):
        """ Parse JSON to get video frames and corresponding captions """
        data = []

        for video_id, info in self.annotations['database'].items():
            if video_id not in self.existing_video_ids:
                continue

            for annotation_idx, annotation in enumerate(info['annotations']):
                sentence = annotation["sentence"]
                sentence_folder = f"{video_id}_sentence{annotation_idx}_frames"
                video_path = os.path.join(self.frame_path, sentence_folder)

                if not os.path.exists(video_path):
                    continue

                # Get `frame_*.jpg` files
                frames = sorted(glob.glob(os.path.join(video_path, "frame_*.jpg")))
                if not frames:
                    continue

                data.append((frames[:8], sentence))  # Select the first 8 frames

        return data

    def __len__(self):
        return len(self.data)

    def __getitem__(self, idx):
        frame_paths, sentence = self.data[idx]
        frames = torch.stack([self.transform(Image.open(fp).convert("RGB")) for fp in frame_paths])
        return frames, sentence

dataset = YouCook2Dataset(annotation_path, frame_dir)
print("Dataset loaded successfully, total samples:", len(dataset))


Dataset loaded successfully, total samples: 8634


In [ ]:
# !pip install --upgrade transformers accelerate diffusers imageio-ffmpeg
import torch
import gc
import numpy as np
from diffusers import AnimateDiffPipeline, MotionAdapter, EulerDiscreteScheduler
from diffusers.utils import export_to_gif
from huggingface_hub import hf_hub_download
from safetensors.torch import load_file
from torch.utils.data import DataLoader
from torch.optim.lr_scheduler import CosineAnnealingLR
from peft import LoraConfig, get_peft_model

device = "cuda"
dtype = torch.float16

step = 4  # Options: [1,2,4,8]
repo = "ByteDance/AnimateDiff-Lightning"
ckpt = f"animatediff_lightning_{step}step_diffusers.safetensors"
base = "emilianJR/epiCRealism"  # Choose the base model.

adapter = MotionAdapter().to(device, dtype)
adapter.load_state_dict(load_file(hf_hub_download(repo, ckpt), device=device))
pipe = AnimateDiffPipeline.from_pretrained(base, motion_adapter=adapter, torch_dtype=dtype).to(device)
pipe.scheduler = EulerDiscreteScheduler.from_config(pipe.scheduler.config, timestep_spacing="trailing", beta_schedule="linear")


# Load pre-trained MotionAdapter
repo = "ByteDance/AnimateDiff-Lightning"
ckpt = f"animatediff_lightning_{step}step_diffusers.safetensors"

adapter = MotionAdapter().to(device, dtype)
adapter.load_state_dict(load_file(hf_hub_download(repo, ckpt), device=device))  # Load the official MotionAdapter pre-trained model
adapter.train()  # Set to training mode

# Enable training for the entire MotionAdapter
for param in adapter.parameters():
    param.requires_grad = True

# Training parameters
num_epochs = 10
learning_rate = 3e-5
max_batches = 50  # Train more batches

# Create DataLoader
dataloader = DataLoader(dataset, batch_size=1, shuffle=True)
optimizer = AdamW(adapter.parameters(), lr=learning_rate)
scheduler = CosineAnnealingLR(optimizer, T_max=num_epochs // 2, eta_min=1e-6)  # Smooth learning rate decay

# Attach the fine-tuned MotionAdapter
pipe.motion_adapter = adapter

# Train MotionAdapter (without LoRA)
for epoch in range(num_epochs):
    epoch_loss = 0
    for batch_idx, batch in enumerate(tqdm(dataloader, desc=f"Epoch {epoch+1}/{num_epochs}")):
        if batch_idx >= max_batches:
            break  # Train only the first 50 batches
        optimizer.zero_grad()

        # Load input data
        frames, captions = batch
        frames = frames.to(device, dtype)  # [batch, frames, channels, height, width]

        # Process text input
        if isinstance(captions, tuple):
            prompts = [str(c) for c in captions]
        elif isinstance(captions, list):
            prompts = [str(c) for c in captions]
        else:
            prompts = [str(captions)]
        prompt = " ".join(prompts)

        # Generate animation
        output = pipe(prompt=prompt, guidance_scale=1.0, num_inference_steps=step)

        # Ensure output.frames is a NumPy array
        frames_np = np.array(output.frames)
        print(f"Shape of output.frames: {frames_np.shape}")  # Debugging

        # Ensure output.frames shape is (frames, H, W, C)
        if frames_np.ndim == 5:  # Possibly (batch, frames, H, W, C)
            frames_np = frames_np.squeeze(0)  # Remove batch dimension

        # Convert to PyTorch Tensor, ensure requires_grad=True
        generated_frames = torch.as_tensor(frames_np, device=device, dtype=dtype).clone().detach().requires_grad_() / 255.0

        # Adjust channel order (frames, H, W, C) -> (frames, C, H, W)
        generated_frames = generated_frames.permute(0, 3, 1, 2)

        # Add batch dimension (batch, frames, C, H, W)
        generated_frames = generated_frames.unsqueeze(0)

        # Interpolate only supports (N, C, H, W), so flatten frames dimension first
        b, f, c, h, w = generated_frames.shape
        generated_frames = generated_frames.view(b * f, c, h, w)

        # Resize to 256x256
        generated_frames = torch.nn.functional.interpolate(
            generated_frames, size=(256, 256), mode='bilinear', align_corners=False
        )

        # Restore frames dimension (batch, frames, C, H, W)
        generated_frames = generated_frames.view(b, f, c, 256, 256)

        # Ensure consistent number of frames
        min_frames = min(generated_frames.shape[1], frames.shape[1])
        generated_frames = generated_frames[:, :min_frames, :, :, :]
        frames = frames[:, :min_frames, :, :, :]

        # Ensure frames also require gradients
        frames = frames.clone().detach().requires_grad_()

        # Compute loss
        # loss = F.mse_loss(generated_frames, frames)
        loss = F.smooth_l1_loss(generated_frames, frames, beta=0.5)

        loss.backward()
        optimizer.step()

        epoch_loss += loss.item()

    print(f"Epoch {epoch+1}/{num_epochs}, Loss: {epoch_loss:.4f}")

# Save the fully fine-tuned MotionAdapter
torch.save(adapter.state_dict(), "/content/drive/Shareddrives/DATA 298B Team 8/CODE/motion_adapter_finetuned.pth")
print("Training complete, saved motion_adapter_finetuned.pth")

# Reload the fully fine-tuned MotionAdapter
adapter = MotionAdapter().to(device, dtype)

# Directly load the full fine-tuned MotionAdapter weights
state_dict = torch.load("/content/drive/Shareddrives/DATA 298B Team 8/CODE/motion_adapter_finetuned.pth", map_location=device)  # No need for `weights_only=True`
adapter.load_state_dict(state_dict, strict=True)  # `strict=True` ensures weights match exactly

pipe = AnimateDiffPipeline.from_pretrained(base, motion_adapter=adapter, torch_dtype=dtype).to(device)
pipe.scheduler = EulerDiscreteScheduler.from_config(pipe.scheduler.config, timestep_spacing="trailing", beta_schedule="linear")

output = pipe(prompt="crack two eggs into a bowl", guidance_scale=1.0, num_inference_steps=step)
export_to_gif(output.frames[0], "/content/drive/Shareddrives/DATA 298B Team 8/CODE/AnimateDiff_finetuned_animation.gif")


Loading pipeline components...:   0%|          | 0/6 [00:00<?, ?it/s]

/usr/local/lib/python3.11/dist-packages/transformers/models/clip/feature_extraction_clip.py:28: FutureWarning: The class CLIPFeatureExtractor is deprecated and will be removed in version 5 of Transformers. Please use CLIPImageProcessor instead.
  warnings.warn(
Epoch 1/10:   0%|          | 0/8634 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

Epoch 1/10:   0%|          | 1/8634 [00:07<18:04:26,  7.54s/it]

Shape of output.frames: (1, 16, 512, 512, 3)


...

Epoch 10/10, Loss: 6.4083
Training complete, saved motion_adapter_finetuned.pth


<ipython-input-7-c64e8ef01eec>:132: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  state_dict = torch.load("/content/drive/Shareddrives/DATA 298B Team 8/CODE/motion_adapter_f

Loading pipeline components...:   0%|          | 0/6 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

'/content/drive/Shareddrives/DATA 298B Team 8/CODE/AnimateDiff_finetuned_animation.gif'

In [ ]:
!pip install gradio diffusers huggingface_hub safetensors torch torchvision

import gradio as gr
import torch
import numpy as np
from diffusers import AnimateDiffPipeline, MotionAdapter, EulerDiscreteScheduler
from huggingface_hub import hf_hub_download
from safetensors.torch import load_file
from PIL import Image

# Define Gradio processing function
def generate_animation(prompt):
    """Generate an animation based on the user input text."""
    output = pipe(prompt=prompt, guidance_scale=1.0, num_inference_steps=step)

    # Ensure output is in NumPy format
    frames_np = np.array(output.frames, dtype=np.float32)  # Ensure float32 for precision

    # Handle dimensions
    if frames_np.ndim == 5:  # Possibly (batch, frames, H, W, C)
        frames_np = frames_np.squeeze(0)

    # Normalize values to range [0, 1] if they are outside the range
    if frames_np.min() < 0 or frames_np.max() > 1:
        frames_np = (frames_np - frames_np.min()) / (frames_np.max() - frames_np.min())

    # Convert to RGB format (if necessary, some models output BGR or grayscale)
    if frames_np.shape[-1] == 3:  # Assuming (frames, H, W, C)
        frames_np = frames_np[..., ::-1]  # Convert BGR to RGB if necessary

    # Convert NumPy array to PIL format
    frames_pil = [Image.fromarray((frame * 255).astype(np.uint8), mode="RGB") for frame in frames_np]

    # Generate GIF
    gif_path = "/content/generated_animation.gif"
    frames_pil[0].save(gif_path, save_all=True, append_images=frames_pil[1:], duration=100, loop=0)

    return gif_path

# Create Gradio interface
interface = gr.Interface(
    fn=generate_animation,
    inputs=gr.Textbox(label="Enter a text prompt"),
    outputs=gr.Image(type="filepath", label="Generated Animation"),
    title="Text to Video Web App",
    description="Enter a text description and generate an animation."
)

# Launch Web App
interface.launch(share=True)


Colab notebook detected. To show errors in colab notebook, set debug=True in launch()
* Running on public URL: https://08008f3358ae9b0d96.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


In [ ]:
!pip install lpips

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 53.8/53.8 kB 4.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 3.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 108.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 86.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 48.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 1.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 10.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 37.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 17.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 5.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 86.5 MB/s eta 0:00:00
  Attempting uninstall: nvidia-nvjitlink-cu12
    Found existing installation: nvidia-nvjitlink-cu12 12.5.82
    Uninstall

# Compute all evaluation metrics for each comparison

In [ ]:
import imageio
import numpy as np
import torch
import torchvision.transforms as transforms
from skimage.metrics import structural_similarity as ssim
from skimage.metrics import peak_signal_noise_ratio as psnr
import lpips
import cv2
import pandas as pd
from scipy.linalg import sqrtm

# Ensure GPU usage
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load GIF files from user-provided paths
file_paths = {
    "original": "Animate1.gif",  # Pre-trained model result
    "2epochs": "Animate2.gif",  # Another comparison GIF
    "10epochs": "Animate3.gif",  # Fine-tuned model result
}

# Load GIF and convert to tensor
def load_gif_frames(file_path, max_frames=3, resize=(64, 64)):
    gif = imageio.mimread(file_path)
    num_frames = min(len(gif), max_frames)
    transform = transforms.Compose([
        transforms.Resize(resize),
        transforms.ToTensor()
    ])
    frames = torch.stack([transform(transforms.ToPILImage()(gif[i])) for i in np.linspace(0, len(gif)-1, num_frames, dtype=int)])
    return frames.to(device)

# Load all GIFs
gif_frames = {key: load_gif_frames(path) for key, path in file_paths.items()}

# Compute SSIM
def compute_avg_ssim(frames1, frames2):
    min_frames = min(frames1.shape[0], frames2.shape[0])
    frames1, frames2 = frames1[:min_frames].cpu().numpy(), frames2[:min_frames].cpu().numpy()

    ssim_values = [
        ssim(frames1[i].mean(axis=0), frames2[i].mean(axis=0), data_range=1.0)
        for i in range(min_frames)
    ]
    return np.mean(ssim_values)

# Compute PSNR
def compute_avg_psnr(frames1, frames2):
    min_frames = min(frames1.shape[0], frames2.shape[0])
    frames1, frames2 = frames1[:min_frames].cpu().numpy(), frames2[:min_frames].cpu().numpy()

    psnr_values = [
        psnr(frames1[i], frames2[i], data_range=1.0)
        for i in range(min_frames)
    ]
    return np.mean(psnr_values)

# Compute LPIPS (Perceptual Loss)
loss_fn = lpips.LPIPS(net='alex').to(device)

def compute_avg_lpips(frames1, frames2):
    min_frames = min(frames1.shape[0], frames2.shape[0])
    lpips_values = [
        loss_fn(frames1[i].unsqueeze(0), frames2[i].unsqueeze(0)).item()
        for i in range(min_frames)
    ]
    return np.mean(lpips_values)

# Compute FVD (Optimized Version)
def compute_fvd(frames1, frames2):
    frames1, frames2 = frames1.view(frames1.shape[0], -1).cpu().numpy(), frames2.view(frames2.shape[0], -1).cpu().numpy()

    mu1, sigma1 = np.mean(frames1, axis=0), np.cov(frames1, rowvar=False)
    mu2, sigma2 = np.mean(frames2, axis=0), np.cov(frames2, rowvar=False)

    tr_sigma = np.trace(sigma1) + np.trace(sigma2) - 2 * np.sqrt(np.trace(sigma1) * np.trace(sigma2))
    return np.sum((mu1 - mu2) ** 2) + tr_sigma

# Compute Optical Flow (Motion Consistency)
def compute_optical_flow(frames):
    flows = []
    for i in range(len(frames) - 1):
        prev, nxt = frames[i].cpu().numpy().transpose(1, 2, 0), frames[i + 1].cpu().numpy().transpose(1, 2, 0)
        prev_gray, nxt_gray = cv2.cvtColor(prev, cv2.COLOR_RGB2GRAY), cv2.cvtColor(nxt, cv2.COLOR_RGB2GRAY)
        flow = cv2.calcOpticalFlowFarneback(prev_gray, nxt_gray, None, 0.5, 3, 15, 3, 5, 1.2, 0)
        flows.append(np.mean(np.abs(flow)))
    return np.mean(flows)

# Compute all evaluation metrics for each comparison
comparisons = {
    "2epochs vs Original": ("original", "2epochs"),
    "10epochs vs Original": ("original", "10epochs"),
    "10epochs vs 2epochs": ("2epochs", "10epochs"),
}

results = {}
for name, (gif1, gif2) in comparisons.items():
    results[name] = {
        "SSIM": compute_avg_ssim(gif_frames[gif1], gif_frames[gif2]),
        "PSNR": compute_avg_psnr(gif_frames[gif1], gif_frames[gif2]),
        "LPIPS": compute_avg_lpips(gif_frames[gif1], gif_frames[gif2]),
        "FVD": compute_fvd(gif_frames[gif1], gif_frames[gif2]),
        "Optical Flow": compute_optical_flow(gif_frames[gif2]),
    }

# Display results
df_results = pd.DataFrame(results).T
from IPython.display import display
display(df_results)


Setting up [LPIPS] perceptual loss: trunk [alex], v[0.1], spatial [off]
Loading model from: /usr/local/lib/python3.11/dist-packages/lpips/weights/v0.1/alex.pth


SSIM       PSNR     LPIPS          FVD  Optical Flow
2epochs vs Original   0.011030  10.244824  0.121561  1068.556276  5.618801e-06
10epochs vs Original  0.368774  13.977532  0.077735   489.256303  8.677052e-07
10epochs vs 2epochs  -0.004966   9.984358  0.142706  1223.179832  8.677052e-07

# Gradio Web Test on motion_adapter_finetuned.pth Weights

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

import torch
from diffusers import AnimateDiffPipeline, MotionAdapter, EulerDiscreteScheduler
from diffusers.utils import export_to_gif
from huggingface_hub import hf_hub_download
from safetensors.torch import load_file

device = "cuda"
dtype = torch.float16

step = 4  # Options: [1,2,4,8]
repo = "ByteDance/AnimateDiff-Lightning"
ckpt = f"animatediff_lightning_{step}step_diffusers.safetensors"
base = "emilianJR/epiCRealism"  # Choose the base model.

adapter = MotionAdapter().to(device, dtype)
adapter.load_state_dict(load_file(hf_hub_download(repo, ckpt), device=device))
pipe = AnimateDiffPipeline.from_pretrained(base, motion_adapter=adapter, torch_dtype=dtype).to(device)
pipe.scheduler = EulerDiscreteScheduler.from_config(pipe.scheduler.config, timestep_spacing="trailing", beta_schedule="linear")

# Directly load the full fine-tuned MotionAdapter weights
state_dict = torch.load("/content/drive/Shareddrives/DATA 298B Team 8/CODE/motion_adapter_finetuned.pth", map_location=device)  # No need for `weights_only=True`
adapter.load_state_dict(state_dict, strict=True)  # `strict=True` ensures weights match exactly

pipe = AnimateDiffPipeline.from_pretrained(base, motion_adapter=adapter, torch_dtype=dtype).to(device)
pipe.scheduler = EulerDiscreteScheduler.from_config(pipe.scheduler.config, timestep_spacing="trailing", beta_schedule="linear")

output = pipe(prompt="crack two eggs into a bowl", guidance_scale=1.0, num_inference_steps=step)
export_to_gif(output.frames[0], "/content/drive/Shareddrives/DATA 298B Team 8/CODE/AnimateDiff_finetuned_animation.gif")

!pip install gradio diffusers huggingface_hub safetensors torch torchvision

import gradio as gr
import torch
import numpy as np
from diffusers import AnimateDiffPipeline, MotionAdapter, EulerDiscreteScheduler
from huggingface_hub import hf_hub_download
from safetensors.torch import load_file
from PIL import Image

# Define Gradio processing function
def generate_animation(prompt):
    """Generate an animation based on the user input text."""
    output = pipe(prompt=prompt, guidance_scale=1.0, num_inference_steps=step)

    # Ensure output is in NumPy format
    frames_np = np.array(output.frames, dtype=np.float32)  # Ensure float32 for precision

    # Handle dimensions
    if frames_np.ndim == 5:  # Possibly (batch, frames, H, W, C)
        frames_np = frames_np.squeeze(0)

    # Normalize values to range [0, 1] if they are outside the range
    if frames_np.min() < 0 or frames_np.max() > 1:
        frames_np = (frames_np - frames_np.min()) / (frames_np.max() - frames_np.min())

    # Convert to RGB format (if necessary, some models output BGR or grayscale)
    if frames_np.shape[-1] == 3:  # Assuming (frames, H, W, C)
        frames_np = frames_np[..., ::-1]  # Convert BGR to RGB if necessary

    # Convert NumPy array to PIL format
    frames_pil = [Image.fromarray((frame * 255).astype(np.uint8), mode="RGB") for frame in frames_np]

    # Generate GIF
    gif_path = "/content/generated_animation.gif"
    frames_pil[0].save(gif_path, save_all=True, append_images=frames_pil[1:], duration=100, loop=0)

    return gif_path

# Create Gradio interface
interface = gr.Interface(
    fn=generate_animation,
    inputs=gr.Textbox(label="Enter a text prompt"),
    outputs=gr.Image(type="filepath", label="Generated Animation"),
    title="Text to Video Web App",
    description="Enter a text description and generate an animation."
)

# Launch Web App
interface.launch(share=True)

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


Loading pipeline components...:   0%|          | 0/6 [00:00<?, ?it/s]

/usr/local/lib/python3.11/dist-packages/transformers/models/clip/feature_extraction_clip.py:28: FutureWarning: The class CLIPFeatureExtractor is deprecated and will be removed in version 5 of Transformers. Please use CLIPImageProcessor instead.
  warnings.warn(
<ipython-input-9-ee99824d57fc>:24: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weight

Loading pipeline components...:   0%|          | 0/6 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

Colab notebook detected. To show errors in colab notebook, set debug=True in launch()
* Running on public URL: https://f7da19cf8897a35b94.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)
